In [1]:
import os
import json
import pandas as pd
import pysrt
import re

In [2]:
def save_json(content, save_path):
    with open(save_path, 'w') as f:
        f.write(json.dumps(content))
def load_jsonl(filename):
    with open(filename, "r") as f:
        return [json.loads(l.strip("\n")) for l in f.readlines()]
def load_result_json(filename):
    with open(filename, "r") as f:
        data = json.load(f)
    print(data)
    return data

In [3]:
eval_folder = "/home/hlpark/REDUCE/REDUCE_benchmarks/HiREST/data/evaluation/tvqa"
if not os.path.exists(eval_folder):
    os.makedirs(eval_folder)

vid_json_folder = "/home/hlpark/REDUCE/REDUCE_benchmarks/HiREST/data/splits/tvqa"
if not os.path.exists(vid_json_folder):
    os.makedirs(vid_json_folder)

val_result_json_path = f"{vid_json_folder}/all_data_val_moment_retrieval_BEST_without_audio.json"
test_result_json_path = f"{vid_json_folder}/all_data_test_moment_retrieval_BEST_without_audio.json"
val_result_wa_json_path = f"{vid_json_folder}/all_data_val_moment_retrieval_BEST_with_audio.json"
test_result_wa_json_path = f"{vid_json_folder}/all_data_test_moment_retrieval_BEST_with_audio.json"

In [4]:
val = load_jsonl(f'{vid_json_folder}/all_data_val.json')
test = load_jsonl(f'{vid_json_folder}/all_data_test.json')
#clip_pred_med = load_jsonl(f'{vid_json_folder}/five_labeled_pred_med_vid_dict.json')

clip_pred_med = load_jsonl(f'{vid_json_folder}/five_labeled_pred_med_from_gt_vid_dict.json')
test_result = load_result_json(test_result_json_path)
val_result = load_result_json(val_result_json_path)
hirest_test_wa_result = load_result_json(test_result_wa_json_path)
hirest_val_wa_result = load_result_json(val_result_wa_json_path)

{"Who does Sheldon say he'll send an email to after coming out of the bathroom?": {'s03e21_seg02_clip_08.mp4': {'bounds': [0, 60], 'video_duration': 61}}, 'How long did Gina say he was on the phone with Castle after Gine introduced herself?': {'castle_s02e24_seg02_clip_26.mp4': {'bounds': [0, 88], 'video_duration': 89}}, 'Where did Masters actually go after she left the operating room?': {'house_s07e19_seg02_clip_12.mp4': {'bounds': [0, 97], 'video_duration': 98}}, 'How did Addie try to kill herself when House found out why she was in that condition?': {'house_s03e22_seg02_clip_23.mp4': {'bounds': [0, 89], 'video_duration': 90}}, 'What is House holding when Wilson stands up and leaves?': {'house_s04e03_seg02_clip_06.mp4': {'bounds': [0, 92], 'video_duration': 93}}, 'What is Cameron looking into before House walks into the office?': {'house_s01e08_seg02_clip_03.mp4': {'bounds': [0, 89], 'video_duration': 90}}, 'What does Beckett hold in her hand when she approaches the man? ': {'castle_

In [5]:
def compute_iou(interval_1, interval_2):
    start_i, end_i = float(interval_1[0]), float(interval_1[1])
    start, end = float(interval_2[0]), float(interval_2[1])
    intersection = max(0, min(end, end_i) - max(start, start_i))
    union = min(max(end, end_i) - min(start, start_i), end-start + end_i-start_i)
    iou = float(intersection) / (union + 1e-8)
    return iou

In [6]:
def save_categorized_data(low_thresh, high_thresh, iou, dict, key, vid, value, pred):
    # if "house" in vid or "grey" in vid:
    #     category = "med"
    # else: 
    #     category = "nonmed"
    category= "all"
    if iou < low_thresh:
        div = "low"
    elif iou >= high_thresh:
        div = "high"
    else:
        return
    if 'queries' not in dict[category][div]:
        dict[category][div]['queries'] = []
        dict[category][div]['videos'] = []
        dict[category][div]['duration'] = []
        dict[category][div]['gt_time_span'] = []
        dict[category][div]['pred_time_span'] = []
        dict[category][div]['iou'] = []
    else:
        dict[category][div]['queries'].append(key)
        dict[category][div]['videos'].append(vid)
        dict[category][div]['duration'].append(value[vid]['v_duration'])
        dict[category][div]['gt_time_span'].append([float(value[vid]['bounds'][1]) , float(value[vid]['bounds'][0])])
        dict[category][div]['pred_time_span'].append([float(pred[key][vid]['bounds'][1]) , float(pred[key][vid]['bounds'][0])])
        dict[category][div]['iou'].append(iou)
    

In [7]:
test_med_queries_path = "/home/hlpark/shared/TVQA/output_gpt_tvqa_test_queries.txt"
val_med_queries_path = "/home/hlpark/shared/TVQA/output_gpt_tvqa_val_queries.txt"
test_med_query_f_metamap_list, val_med_query_f_metamap_list = [], []
with open(test_med_queries_path, "r") as f:
    lines = f.read()
    for line in lines.split("\n"):
        if line == "\n" or line == "":
            continue
        if line.startswith(" ") or line.startswith("-"):
            line = line.lstrip("-").lstrip(" ")
        test_med_query_f_metamap_list.append(line.lower().replace(" ", "").replace("?", "").replace("\n", "").replace("-", "").replace("'", "").replace("\"", "").replace(",", "").replace(".", "").replace("/", "").replace(">", ""))
f.close()
with open(val_med_queries_path, "r") as f:
    lines = f.read()
    for line in lines.split("\n"):
        if line == "\n" or line == "":
            continue
        # if line.startswith(" ") or line.startswith("-"):
        #     line = line.lstrip("-").lstrip(" ")
        val_med_query_f_metamap_list.append(line.lower().replace(" ", "").replace("?", "").replace("\n", "").replace("-", "").replace("'", "").replace("\"", "").replace(",", "").replace(".", "").replace("/", "").replace(">", ""))
        #val_med_query_f_metamap_list.append(line.strip(" ").strip("\n").replace("  ", " "))
f.close()
print(len(test_med_query_f_metamap_list), len(val_med_query_f_metamap_list))

246 569


In [8]:
select_option = "med_queries"
# select_option = "med_samples_clip_from_gt"
# select_option = "med_samples_clip_full_rand"
# select_option = "tv shows"

In [9]:
print("HiREST without Audio " + select_option)
iou_thresh_3, iou_thresh_5, iou_thresh_7, total, queries_cnt = 0, 0, 0, 0, 0
med_iou_thresh_3, med_iou_thresh_5, med_iou_thresh_7, med_total = 0, 0, 0, 0
nonmed_iou_thresh_3, nonmed_iou_thresh_5, nonmed_iou_thresh_7, nonmed_total = 0, 0, 0, 0
test_woa_under_thresh, test_wa_under_thresh, val_woa_under_thresh, val_wa_under_thresh = {'all': {'low':{}, 'high': {}}}, {'all': {'low':{}, 'high': {}}}, {'all': {'low':{}, 'high': {}}}, {'all': {'low':{}, 'high': {}}}
for key, value in test[0].items():
    if key in test_result:
        vid = next(iter(value))
        #print(value[vid]['bounds'])

        iou = compute_iou(value[vid]['bounds'], test_result[key][vid]['bounds'])
        save_categorized_data(0.3, 0.3, iou, test_woa_under_thresh, key, vid, value, test_result)
        if iou >= 0.3:
            iou_thresh_3 += 1 
        if iou >= 0.5:
            iou_thresh_5 += 1 
        if iou >= 0.7:
            iou_thresh_7 += 1 
        total += 1
        ismed = False
        if select_option == "tv shows":
            if "house" in vid or "grey" in vid:
                ismed = True
        elif select_option == "med_samples_clip_full_rand":
            if clip_pred_med[0][vid] == "med":
               ismed = True
        elif select_option == "med_samples_clip_from_gt":
            for qc in clip_pred_med[0][vid.replace(".mp4", "")]:
                #print(qc)
                if key in qc and qc[key] == "med":
                    ismed = True
        elif select_option == "med_queries":
            newkey = key.lower().replace(" ", "").replace("?", "").replace("\n", "").replace("-", "").replace("'", "").replace("\"", "").replace(">", "").replace(",", "").replace(".", "").replace("/", "")
            if newkey  in test_med_query_f_metamap_list:
                ismed = True
        if ismed:
            med_total += 1
            if iou >= 0.3:
                med_iou_thresh_3 += 1 
            if iou >= 0.5:
                med_iou_thresh_5 += 1 
            if iou >= 0.7:
                med_iou_thresh_7 += 1 
        else:
            nonmed_total += 1
            if iou >= 0.3:
                nonmed_iou_thresh_3 += 1 
            if iou >= 0.5:
                nonmed_iou_thresh_5 += 1 
            if iou >= 0.7:
                nonmed_iou_thresh_7 += 1 
    else:
        print("Not found")
    queries_cnt += 1

print(f"TEST IoU=0.3: {iou_thresh_3/(total) * 100}\nIoU=0.5: {iou_thresh_5/(total) * 100}\nIoU=0.7: {iou_thresh_7/(total) * 100}\ntotal queries:{(total)}/{queries_cnt}")
print(med_iou_thresh_3, nonmed_iou_thresh_3, med_total, nonmed_total)
print(f"TEST Medical IoU=0.3: {med_iou_thresh_3/(med_total) * 100}\nIoU=0.5: {med_iou_thresh_5/(med_total) * 100}\nIoU=0.7: {med_iou_thresh_7/(med_total) * 100}\ntotal queries:{(med_total)}/{queries_cnt}")
print(f"TEST Non-Medical IoU=0.3: {nonmed_iou_thresh_3/(nonmed_total) * 100}\nIoU=0.5: {nonmed_iou_thresh_5/(nonmed_total) * 100}\nIoU=0.7: {nonmed_iou_thresh_7/(nonmed_total) * 100}\ntotal queries:{(nonmed_total)}/{queries_cnt}")

iou_thresh_3, iou_thresh_5, iou_thresh_7, total, queries_cnt = 0, 0, 0, 0, 0
med_iou_thresh_3, med_iou_thresh_5, med_iou_thresh_7, med_total = 0, 0, 0, 0
nonmed_iou_thresh_3, nonmed_iou_thresh_5, nonmed_iou_thresh_7, nonmed_total = 0, 0, 0, 0
for key, value in val[0].items():
    if key in val_result:
        vid = next(iter(value))
        #print(vid)
        iou = compute_iou(value[vid]['bounds'], val_result[key][vid]['bounds'])
        save_categorized_data(0.3, 0.3, iou, val_woa_under_thresh, key, vid, value, val_result)
        if iou >= 0.3:
            iou_thresh_3 += 1 
        if iou >= 0.5:
            iou_thresh_5 += 1 
        if iou >= 0.7:
            iou_thresh_7 += 1 
        total += 1
        ismed = False
        if select_option == "tv shows":
            if "house" in vid or "grey" in vid:
                ismed = True
        elif select_option == "med_samples_clip_full_rand":
            if clip_pred_med[0][vid] == "med":
               ismed = True
        elif select_option == "med_samples_clip_from_gt":
            for qc in clip_pred_med[0][vid.replace(".mp4", "")]:
                #print(qc)
                if key in qc and qc[key] == "med":
                    ismed = True
        elif select_option == "med_queries":
            newkey = key.lower().replace(" ", "").replace("?", "").replace("\n", "").replace("-", "").replace("'", "").replace("\"", "").replace(">", "").replace(",", "").replace(".", "").replace("/", "")
            if newkey  in val_med_query_f_metamap_list:
                ismed = True
        if ismed:
            med_total += 1
            if iou >= 0.3:
                med_iou_thresh_3 += 1 
            if iou >= 0.5:
                med_iou_thresh_5 += 1 
            if iou >= 0.7:
                med_iou_thresh_7 += 1 
        else:
            nonmed_total += 1
            if iou >= 0.3:
                nonmed_iou_thresh_3 += 1 
            if iou >= 0.5:
                nonmed_iou_thresh_5 += 1 
            if iou >= 0.7:
                nonmed_iou_thresh_7 += 1 
    else:
        print(f" not found")
    queries_cnt += 1

print(f"\n\nVAL IoU=0.3: {iou_thresh_3/(total) * 100}\nIoU=0.5: {iou_thresh_5/(total) * 100}\nIoU=0.7: {iou_thresh_7/(total) * 100}\ntotal queries:{(total)}/{queries_cnt}")
print(med_iou_thresh_3, nonmed_iou_thresh_3, med_total, nonmed_total)
print(f"VAL Medical IoU=0.3: {med_iou_thresh_3/(med_total) * 100}\nIoU=0.5: {med_iou_thresh_5/(med_total) * 100}\nIoU=0.7: {med_iou_thresh_7/(med_total) * 100}\ntotal queries:{(med_total)}/{queries_cnt}")
print(f"VAL Non-Medical IoU=0.3: {nonmed_iou_thresh_3/(nonmed_total) * 100}\nIoU=0.5: {nonmed_iou_thresh_5/(nonmed_total) * 100}\nIoU=0.7: {nonmed_iou_thresh_7/(nonmed_total) * 100}\ntotal queries:{(nonmed_total)}/{queries_cnt}")


HiREST without Audio med_queries
TEST IoU=0.3: 10.120766605408244
IoU=0.5: 5.907062221055395
IoU=0.7: 3.478603307954844
total queries:7618/7618
14 757 246 7372
TEST Medical IoU=0.3: 5.691056910569105
IoU=0.5: 2.8455284552845526
IoU=0.7: 2.4390243902439024
total queries:246/7618
TEST Non-Medical IoU=0.3: 10.268583830710797
IoU=0.5: 6.009224091155724
IoU=0.7: 3.5132935431361907
total queries:7372/7618




VAL IoU=0.3: 10.581212280241406
IoU=0.5: 5.077407504591971
IoU=0.7: 2.8995014431907635
total queries:15244/15244
44 1569 569 14675
VAL Medical IoU=0.3: 7.732864674868189
IoU=0.5: 2.2847100175746924
IoU=0.7: 1.054481546572935
total queries:569/15244
VAL Non-Medical IoU=0.3: 10.691652470187393
IoU=0.5: 5.185689948892675
IoU=0.7: 2.971039182282794
total queries:14675/15244


In [10]:
print("HiREST with audio " + select_option)
iou_thresh_3, iou_thresh_5, iou_thresh_7, total, queries_cnt = 0, 0, 0, 0, 0
med_iou_thresh_3, med_iou_thresh_5, med_iou_thresh_7, med_total = 0, 0, 0, 0
nonmed_iou_thresh_3, nonmed_iou_thresh_5, nonmed_iou_thresh_7, nonmed_total = 0, 0, 0, 0

for key, value in test[0].items():
    if key in hirest_test_wa_result:
        vid = next(iter(value))
        #print(value[vid]['bounds'])

        iou = compute_iou(value[vid]['bounds'], hirest_test_wa_result[key][vid]['bounds'])
        save_categorized_data(0.3, 0.3, iou, test_wa_under_thresh, key, vid, value, hirest_test_wa_result)
        if iou >= 0.3:
            iou_thresh_3 += 1 
        if iou >= 0.5:
            iou_thresh_5 += 1 
        if iou >= 0.7:
            iou_thresh_7 += 1 
        total += 1
        ismed = False
        if select_option == "tv shows":
            if "house" in vid or "grey" in vid:
                ismed = True
        elif select_option == "med_samples_clip_full_rand":
            if clip_pred_med[0][vid] == "med":
               ismed = True
        elif select_option == "med_samples_clip_from_gt":
            for qc in clip_pred_med[0][vid.replace(".mp4", "")]:
                #print(qc)
                if key in qc and qc[key] == "med":
                    ismed = True
        elif select_option == "med_queries":
            newkey = key.lower().replace(" ", "").replace("?", "").replace("\n", "").replace("-", "").replace("'", "").replace("\"", "").replace(">", "").replace(",", "").replace(".", "").replace("/", "")
            if newkey  in test_med_query_f_metamap_list:
                ismed = True
        if ismed:
            med_total += 1
            if iou >= 0.3:
                med_iou_thresh_3 += 1 
            if iou >= 0.5:
                med_iou_thresh_5 += 1 
            if iou >= 0.7:
                med_iou_thresh_7 += 1 
        else:
            nonmed_total += 1
            if iou >= 0.3:
                nonmed_iou_thresh_3 += 1 
            if iou >= 0.5:
                nonmed_iou_thresh_5 += 1 
            if iou >= 0.7:
                nonmed_iou_thresh_7 += 1 
    else:
        print("Not found")
    queries_cnt += 1
print(f"TEST IoU=0.3: {iou_thresh_3/(total) * 100}\nIoU=0.5: {iou_thresh_5/(total) * 100}\nIoU=0.7: {iou_thresh_7/(total) * 100}\ntotal queries:{(total)}/{queries_cnt}")
print(f"TEST Medical IoU=0.3: {med_iou_thresh_3/(med_total) * 100}\nIoU=0.5: {med_iou_thresh_5/(med_total) * 100}\nIoU=0.7: {med_iou_thresh_7/(med_total) * 100}\ntotal queries:{(med_total)}/{queries_cnt}")
print(f"TEST Non-Medical IoU=0.3: {nonmed_iou_thresh_3/(nonmed_total) * 100}\nIoU=0.5: {nonmed_iou_thresh_5/(nonmed_total) * 100}\nIoU=0.7: {nonmed_iou_thresh_7/(nonmed_total) * 100}\ntotal queries:{(nonmed_total)}/{queries_cnt}")

iou_thresh_3, iou_thresh_5, iou_thresh_7, total, queries_cnt = 0, 0, 0, 0, 0
med_iou_thresh_3, med_iou_thresh_5, med_iou_thresh_7, med_total = 0, 0, 0, 0
nonmed_iou_thresh_3, nonmed_iou_thresh_5, nonmed_iou_thresh_7, nonmed_total = 0, 0, 0, 0
for key, value in val[0].items():
    if key in hirest_val_wa_result:
        vid = next(iter(value))
        #print(vid)
        iou = compute_iou(value[vid]['bounds'], hirest_val_wa_result[key][vid]['bounds'])
        save_categorized_data(0.3, 0.3, iou, val_wa_under_thresh, key, vid, value, hirest_val_wa_result)
        if iou >= 0.3:
            iou_thresh_3 += 1 
        if iou >= 0.5:
            iou_thresh_5 += 1 
        if iou >= 0.7:
            iou_thresh_7 += 1 
        total += 1
        ismed = False
        if select_option == "tv shows":
            if "house" in vid or "grey" in vid:
                ismed = True
        elif select_option == "med_samples_clip_full_rand":
            if clip_pred_med[0][vid] == "med":
               ismed = True
        elif select_option == "med_samples_clip_from_gt":
            for qc in clip_pred_med[0][vid.replace(".mp4", "")]:
                #print(qc)
                if key in qc and qc[key] == "med":
                    ismed = True
        elif select_option == "med_queries":
            newkey = key.lower().replace(" ", "").replace("?", "").replace("\n", "").replace("-", "").replace("'", "").replace("\"", "").replace(">", "").replace(",", "").replace(".", "").replace("/", "")
            if newkey  in val_med_query_f_metamap_list:
                ismed = True
        if ismed:
            med_total += 1
            if iou >= 0.3:
                med_iou_thresh_3 += 1 
            if iou >= 0.5:
                med_iou_thresh_5 += 1 
            if iou >= 0.7:
                med_iou_thresh_7 += 1 
        else:
            nonmed_total += 1
            if iou >= 0.3:
                nonmed_iou_thresh_3 += 1 
            if iou >= 0.5:
                nonmed_iou_thresh_5 += 1 
            if iou >= 0.7:
                nonmed_iou_thresh_7 += 1 
    else:
        print(f" not found")
    queries_cnt += 1
print(f"\n\nVAL IoU=0.3: {iou_thresh_3/(total) * 100}\nIoU=0.5: {iou_thresh_5/(total) * 100}\nIoU=0.7: {iou_thresh_7/(total) * 100}\ntotal queries:{(total)}/{queries_cnt}")
print(f"VAL Medical IoU=0.3: {med_iou_thresh_3/(med_total) * 100}\nIoU=0.5: {med_iou_thresh_5/(med_total) * 100}\nIoU=0.7: {med_iou_thresh_7/(med_total) * 100}\ntotal queries:{(med_total)}/{queries_cnt}")
print(f"VAL Non-Medical IoU=0.3: {nonmed_iou_thresh_3/(nonmed_total) * 100}\nIoU=0.5: {nonmed_iou_thresh_5/(nonmed_total) * 100}\nIoU=0.7: {nonmed_iou_thresh_7/(nonmed_total) * 100}\ntotal queries:{(nonmed_total)}/{queries_cnt}")


HiREST with audio med_queries
TEST IoU=0.3: 9.477553163559989
IoU=0.5: 5.381990023628249
IoU=0.7: 2.9666579154633763
total queries:7618/7618
TEST Medical IoU=0.3: 4.878048780487805
IoU=0.5: 2.8455284552845526
IoU=0.7: 2.0325203252032518
total queries:246/7618
TEST Non-Medical IoU=0.3: 9.631036353771027
IoU=0.5: 5.4666304937601735
IoU=0.7: 2.9978296256104175
total queries:7372/7618


VAL IoU=0.3: 9.492259249540803
IoU=0.5: 4.460771451062713
IoU=0.7: 2.4665442141170297
total queries:15244/15244
VAL Medical IoU=0.3: 6.6783831282952555
IoU=0.5: 2.6362038664323375
IoU=0.7: 1.054481546572935
total queries:569/15244
VAL Non-Medical IoU=0.3: 9.601362862010221
IoU=0.5: 4.531516183986371
IoU=0.7: 2.5212947189097106
total queries:14675/15244


In [11]:
from tqdm import tqdm
med_cnt = 0
with open("./queries_on_baseline_woa_test_low.txt", "w") as f:
    for idx, question in tqdm(enumerate(test_woa_under_thresh['all']['low']['queries'])):
        q = question.lower().replace(".", "").replace("?", "").replace("-", "")
        vid_show = test_woa_under_thresh['all']['low']['videos'][idx]
        iou = test_woa_under_thresh['all']['low']['iou'][idx]
        gt = test_woa_under_thresh['all']['low']['gt_time_span'][idx]
        pred = test_woa_under_thresh['all']['low']['pred_time_span'][idx]
        ismed = False
        if select_option == "tv shows":
            if "house" in vid_show or "grey" in vid_show:
                ismed = True
        elif select_option == "med_samples_clip_full_rand":
            if clip_pred_med[0][vid_show] == "med":
                ismed = True
        elif select_option == "med_samples_clip_from_gt":
            for qc in clip_pred_med[0][vid_show.replace(".mp4", "")]:
                #print(qc)
                if key in qc and qc[question] == "med":
                    ismed = True
        elif select_option == "med_queries":
            newkey = question.lower().replace(" ", "").replace("?", "").replace("\n", "").replace("-", "").replace("'", "").replace("\"", "").replace(">", "").replace(",", "").replace(".", "").replace("/", "")
            if newkey  in test_med_query_f_metamap_list:
                ismed = True
        if ismed:
            print(vid_show, question, iou, gt, pred)
            med_cnt += 1
            f.writelines(f"{vid_show}, {question}, {iou}, {gt}, {pred} \n")
print(med_cnt)
f.close()

0it [00:00, ?it/s]

6846it [00:00, 88999.04it/s]

house_s03e22_seg02_clip_23.mp4 How did Addie try to kill herself when House found out why she was in that condition? 0.05494382021854561 [27.15, 22.26] [89.0, 0.0]
house_s01e04_seg02_clip_13.mp4 How does Chase react to cope with the baby's deteriorating condition after one of the assisting nurses states she is losing pulse? 0.10222660961914805 [91.17, 80.68] [90.0, 0.0]
house_s04e11_seg02_clip_05.mp4 why did house tell cate to stab herself in the chest after seeing her have trouble breathing? 0.0601086956456403 [57.98, 52.45] [92.0, 0.0]
house_s03e03_seg02_clip_14.mp4 What does Cameron accuse House of doing when House says he is going to perform the laryngoscope?  0.18505494503460937 [20.48, 3.64] [91.0, 0.0]
house_s03e10_seg02_clip_18.mp4 How does Cameron say the patient responded to steroids with her diagnosis before Wilson disagrees with her? 0.11499999998662792 [77.86, 67.97] [86.0, 0.0]
grey_s02e11_seg02_clip_06.mp4 What ribs does the doctor say to stick the needle between after h

In [12]:
med_cnt= 0
with open("./queries_on_baseline_woa_test_high.txt", "w") as f:
    for idx, question in tqdm(enumerate(test_woa_under_thresh['all']['high']['queries'])):
        q = question.lower().replace(".", "").replace("?", "").replace("-", "")
        vid_show = test_woa_under_thresh['all']['high']['videos'][idx]
        iou = test_woa_under_thresh['all']['high']['iou'][idx]
        gt = test_woa_under_thresh['all']['high']['gt_time_span'][idx]
        pred = test_woa_under_thresh['all']['high']['pred_time_span'][idx]
        ismed = False
        if select_option == "tv shows":
            if "house" in vid_show or "grey" in vid_show:
                ismed = True
        elif select_option == "med_samples_clip_full_rand":
            if clip_pred_med[0][vid_show] == "med":
                ismed = True
        elif select_option == "med_samples_clip_from_gt":
            for qc in clip_pred_med[0][vid_show.replace(".mp4", "")]:
                #print(qc)
                if key in qc and qc[question] == "med":
                    ismed = True
        elif select_option == "med_queries":
            newkey = question.lower().replace(" ", "").replace("?", "").replace("\n", "").replace("-", "").replace("'", "").replace("\"", "").replace(">", "").replace(",", "").replace(".", "").replace("/", "")
            if newkey  in test_med_query_f_metamap_list:
                ismed = True
        if ismed:
            print(vid_show, question, iou, gt, pred)
            med_cnt += 1
            f.writelines(f"{vid_show}, {question}, {iou}, {gt}, {pred} \n")
print(med_cnt)
f.close()

770it [00:00, 80444.72it/s]

grey_s02e21_seg02_clip_05.mp4 What did Nikki say she never should have gotten out of when the doctor set her leg? 0.5768416359548822 [89.73, 37.24] [89.0, 0.0]
house_s06e11_seg02_clip_19.mp4 Where did House go after the doctors thought that she might need a liver transplant? 0.8045054944170873 [73.21, 0.0] [91.0, 0.0]
house_s04e13_seg02_clip_09.mp4 Why does Foreman tell House Kutner doesn't think the patient has syphillis but he'll run tests when Kutner goes to test for syphilis because House says to do it? 0.3605555555154939 [55.43, 22.98] [90.0, 0.0]
friends_s04e01_seg02_clip_11.mp4 Why is Phoebe depressed when she comes home? 0.7503571427231506 [45.38, 3.36] [56.0, 0.0]
house_s03e14_seg02_clip_19.mp4 how many metabolic conditions did House state there were when talking to the woman in the beginning? 0.9747833813624992 [90.02, 2.25] [90.0, 0.0]
grey_s02e07_seg02_clip_18.mp4 Where are Burke, George and Mr Griswald when Mr. Griswald recants about a patient. 0.767538912613632 [88.66, 19

In [13]:
from tqdm import tqdm
med_cnt = 0
with open("./queries_on_baseline_wa_test_low.txt", "w") as f:
    for idx, question in tqdm(enumerate(test_wa_under_thresh['all']['low']['queries'])):
        q = question.lower().replace(".", "").replace("?", "").replace("-", "")
        vid_show = test_wa_under_thresh['all']['low']['videos'][idx]
        iou = test_wa_under_thresh['all']['low']['iou'][idx]
        gt = test_wa_under_thresh['all']['low']['gt_time_span'][idx]
        pred = test_wa_under_thresh['all']['low']['pred_time_span'][idx]
        ismed = False
        if select_option == "tv shows":
            if "house" in vid_show or "grey" in vid_show:
                ismed = True
        elif select_option == "med_samples_clip_full_rand":
            if clip_pred_med[0][vid_show] == "med":
                ismed = True
        elif select_option == "med_samples_clip_from_gt":
            for qc in clip_pred_med[0][vid_show.replace(".mp4", "")]:
                #print(qc)
                if key in qc and qc[question] == "med":
                    ismed = True
        elif select_option == "med_queries":
            newkey = question.lower().replace(" ", "").replace("?", "").replace("\n", "").replace("-", "").replace("'", "").replace("\"", "").replace(">", "").replace(",", "").replace(".", "").replace("/", "")
            if newkey  in test_med_query_f_metamap_list:
                ismed = True
        if ismed:
            print(vid_show, question, iou, gt, pred)
            med_cnt += 1
            f.writelines(f"{vid_show}, {question}, {iou}, {gt}, {pred} \n")
print(med_cnt)
f.close()

6895it [00:00, 78785.96it/s]

house_s03e22_seg02_clip_23.mp4 How did Addie try to kill herself when House found out why she was in that condition? 0.0 [27.15, 22.26] [9.0, 9.0]
house_s01e04_seg02_clip_13.mp4 How does Chase react to cope with the baby's deteriorating condition after one of the assisting nurses states she is losing pulse? 0.1069175174822854 [91.17, 80.68] [90.0, 4.0]
house_s04e11_seg02_clip_05.mp4 why did house tell cate to stab herself in the chest after seeing her have trouble breathing? 0.07276315788516267 [57.98, 52.45] [76.0, 0.0]
house_s03e03_seg02_clip_14.mp4 What does Cameron accuse House of doing when House says he is going to perform the laryngoscope?  0.0 [20.48, 3.64] [0.0, 0.0]
house_s03e10_seg02_clip_18.mp4 How does Cameron say the patient responded to steroids with her diagnosis before Wilson disagrees with her? 0.12362499998454689 [77.86, 67.97] [80.0, 0.0]
grey_s02e11_seg02_clip_06.mp4 What ribs does the doctor say to stick the needle between after he says no time? 0.0 [16.91, 12.91]

In [14]:
med_cnt= 0
with open("./queries_on_baseline_wa_test_high.txt", "w") as f:
    for idx, question in tqdm(enumerate(test_wa_under_thresh['all']['high']['queries'])):
        q = question.lower().replace(".", "").replace("?", "").replace("-", "")
        vid_show = test_wa_under_thresh['all']['high']['videos'][idx]
        iou = test_wa_under_thresh['all']['high']['iou'][idx]
        gt = test_wa_under_thresh['all']['high']['gt_time_span'][idx]
        pred = test_wa_under_thresh['all']['high']['pred_time_span'][idx]
        ismed = False
        if select_option == "tv shows":
            if "house" in vid_show or "grey" in vid_show:
                ismed = True
        elif select_option == "med_samples_clip_full_rand":
            if clip_pred_med[0][vid_show] == "med":
                ismed = True
        elif select_option == "med_samples_clip_from_gt":
            for qc in clip_pred_med[0][vid_show.replace(".mp4", "")]:
                #print(qc)
                if key in qc and qc[question] == "med":
                    ismed = True
        elif select_option == "med_queries":
            newkey = question.lower().replace(" ", "").replace("?", "").replace("\n", "").replace("-", "").replace("'", "").replace("\"", "").replace(">", "").replace(",", "").replace(".", "").replace("/", "")
            if newkey  in test_med_query_f_metamap_list:
                ismed = True
        if ismed:
            print(vid_show, question, iou, gt, pred)
            med_cnt += 1
            f.writelines(f"{vid_show}, {question}, {iou}, {gt}, {pred} \n")
print(med_cnt)
f.close()

721it [00:00, 54927.59it/s]

grey_s02e21_seg02_clip_05.mp4 What did Nikki say she never should have gotten out of when the doctor set her leg? 0.5833427250554105 [89.73, 37.24] [89.0, 1.0]
house_s04e13_seg02_clip_09.mp4 Why does Foreman tell House Kutner doesn't think the patient has syphillis but he'll run tests when Kutner goes to test for syphilis because House says to do it? 0.3957317072688133 [55.43, 22.98] [88.0, 6.0]
friends_s04e01_seg02_clip_11.mp4 Why is Phoebe depressed when she comes home? 0.7928301885296547 [45.38, 3.36] [53.0, 0.0]
house_s03e14_seg02_clip_19.mp4 how many metabolic conditions did House state there were when talking to the woman in the beginning? 0.8431126807743976 [90.02, 2.25] [79.0, 5.0]
house_s02e13_seg02_clip_17.mp4 Where does House tell Cuddy he needs a shot of Morphine before he tells her get the syringe? 0.30632352936671725 [63.34, 42.51] [69.0, 1.0]
grey_s02e07_seg02_clip_18.mp4 Where are Burke, George and Mr Griswald when Mr. Griswald recants about a patient. 0.744980825541960